# Code to extract features from images

In [1]:
from google.colab import drive
drive.mount('/content/drive')
#below where the file is in gdrive, change with yours
data_path = "/content/drive/My Drive/VisionAI/Final_Project/"

Mounted at /content/drive


In [ ]:
import pandas as pd
import numpy as np
from tensorflow.keras.preprocessing.text import Tokenizer
from tensorflow.keras.preprocessing.sequence import pad_sequences
import os
import cv2
import tensorflow as tf
from tensorflow.keras.applications import ResNet50
from tensorflow.keras.applications.resnet50 import preprocess_input
from tensorflow.keras.models import Model
from tensorflow.keras.layers import Dense, Embedding, GlobalAveragePooling1D, GlobalAveragePooling2D, concatenate, Add, LSTM, Dropout, Input
from tqdm import tqdm
import tensorflow.keras.utils as keras_utils
from tensorflow.keras.preprocessing import image as keras_image_utils
from PIL import Image
from PIL import UnidentifiedImageError
FEATURE_DIM = 256

In [ ]:
def clean_captions(df):
    # Fill empty captions with a placeholder word if needed, or drop them
    df['caption'] = df['caption'].fillna('')
    # Add start and end sequence markers
    df['caption_seq'] = df['caption'].apply(lambda x: 'startseq ' + x + ' endseq')
    return df

df_cleaned = clean_captions(df)
all_captions = df_cleaned['caption_seq'].tolist()
print(all_captions)

['startseq Nice rock artwork everywhere and craploads of taps. endseq', 'startseq  endseq', 'startseq oyster shooter endseq', 'startseq Shrimp scampi endseq', 'startseq  endseq', 'startseq  endseq', 'startseq  endseq', 'startseq  endseq', 'startseq  endseq', 'startseq Inside reception endseq', 'startseq Small portion of the back patio endseq', 'startseq  endseq', "startseq Fried Chick'un Sandwich endseq", 'startseq The Korrito! Korean BBQ sushi made burrito size! endseq', 'startseq  endseq', 'startseq  endseq', 'startseq Drive-thru menu endseq', 'startseq  endseq', "startseq These cream filled donuts can't be beat!  Cream in every bite guaranteed :) endseq", 'startseq Piedmont Salad--serious yum factor endseq', 'startseq  endseq', 'startseq  endseq', 'startseq  endseq', 'startseq Bulgogi steak tacos. Delicious!!! endseq', 'startseq Lamb Chops endseq', 'startseq Courtyard at Bistro di Marino endseq', 'startseq This was the shareable drink called One Big Swizzle! So fun!! endseq', 'start

/tmp/ipython-input-355287398.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['caption'] = df['caption'].fillna('')
/tmp/ipython-input-355287398.py:5: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['caption_seq'] = df['caption'].apply(lambda x: 'startseq ' + x + ' endseq')


In [ ]:
tokenizer = Tokenizer()
tokenizer.fit_on_texts(all_captions)

VOCAB_SIZE = len(tokenizer.word_index) + 1
MAX_CAPTION_LENGTH = max(len(c.split()) for c in all_captions)
#df_photos = df_photos_with_business.copy()
photo_path = '/content/drive/My Drive/VisionAI/Final_Project/yelp-dataset/photos'
FEATURE_DIM = 256
# Output file to save the features and IDs
output_file = '/content/drive/My Drive/VisionAI/Final_Project/yelp_image_features.npz'

In [ ]:
photo_ids = df['photo_id']
print(photo_ids)

0         zsvj7vloL4L5jhYyPIuVwg
1         HCUdRJHHm_e0OCTlZetGLg
2         vkr8T0scuJmGVvN2HJelEA
3         pve7D6NUrafHW3EAORubyw
4         H52Er-uBg6rNrHcReWTD2w
                   ...          
200095    4Zia9NkAfQNjMfcIDhwJ-g
200096    KB96KRZRhRm8hUkI-OpGEA
200097    Klmojvaf2_2dP1XKzTsFmQ
200098    FNEiq7Mogec7t31OaU5juw
200099    NHEtLh7APk7Yssjo0h45VA
Name: photo_id, Length: 200100, dtype: object


In [ ]:
photo_path = '/content/drive/My Drive/VisionAI/Final_Project/yelp-dataset/photos'
photo_id = ['ydm3g1wUWSxJnMPgHk2JhQ', 'JGpfPj8VEvnq1B-Xqr3w-A', 'bf3ymV0YgP7B6rEoriaU2w', 'juDNZOOnkgG3QINFrulsAg', '9X4YPM8nYFjf7hY8xUdc6Q', 'N6hL8FQ84A2DznF2S2Lp7g', 'pY32hIagdxrL4Nsi959EQg', 'cNkUV0sInfh_Py5PP8SHtQ', 'Pk87_8Yndygr4LRUD_H7Hg', 'ke4ohxa93GJz0KH9H2kwsQ', 'rLafN9k3_AF5lZU0cs3LZg', '-YAvSvGUs2ugiJUvIRO6Jw', 'feUGw0P5byOq4U40C77tyQ', 'pW1IPuTdLIUB61goirbXaA', 'RLtBKD2rlfTaELWejmLBCA', 'IB2ZjqjtS1W_DadQoPPdgg', '43fHlHSYQ_79OBJW1aVUxA', 'QhATx1B1n8uf8C6siMNTfA', '9RDbbAZB0HnL4hndCWB58w', '1wd_eyhMrTqUmicDmn4_Kw', 'W94rrCn0O5K1lkfD26m4tw', 'n6Q9vNuxz7786ESEfautxQ', 'YW1WMOkVbdFBrixDnKgoqA', 'hjEfal2a1DWRDu8_AUDLNg', '0TpeNZPs3Gu8s30KVXudcg', 'AMSyCOP3-Eb_ivNA8w1Vhw', 'TvD36_DdnyCJuXV1SSt3_Q', 'rrfwGSwt3eHxxypfu5PGTA', 'qMlGILrsrzhMDxajNYiyIA', 'jU-dKl2Ye4L_5x602yoctQ', 'TN4-gAea6ejAdZ-NzYXxng', 'IkGbGxI8IoOCuVsNB0VLrA', 'nKJ7yiPc0E_DJNtNxmCrhg', 'E7Wpzn-1fCnVJ8_zKpecPQ', 'MduVueqYTBlEkX-axrh1ug', 'ytJ4lihJrvyzMMRG-WwDNw', '-BIybLxzoFt2d2zbYRcfHA', 'RhC7TNmFvbR9GWrlrl5dsA', 'OK6HsALzFcBAUlrroKHZGg', 'CBxmBYD_5CXIL_F-2PDqmA']
for i in range(len(photo_id)):
  file_name = f"{photo_id[i]}.jpg"
  full_path = os.path.join(photo_path, file_name)

  print(f"\nChecking path: {full_path}")

  # --- Verification ---

  if os.path.exists(full_path):
      print("✅ FILE EXISTENCE CHECK: File is present at the specified path.")

      try:
          # Check integrity and file size
          file_size = os.path.getsize(full_path)
          print(f"Size: {file_size} bytes.")

          if file_size == 0:
              print("❌ INTEGRITY CHECK: File is a **zero-byte file** (empty/corrupted). Cannot be read.")
          else:
              # Attempt to open and verify the image structure using PIL
              with Image.open(full_path) as img:
                  img.verify() # Reads the file header and structure

              print("✅ INTEGRITY CHECK: PIL successfully verified the file structure.")

      except Exception as e:
          # Catches the 'cannot identify image file' error or general corruption
          print(f"❌ INTEGRITY CHECK: PIL FAILED to read the file structure.")
          print(f"   Reason: {e}")
          print("   Action: This file is **corrupted** and must be skipped during extraction.")

  else:
      print("❌ FILE EXISTENCE CHECK: File NOT found at the specified path.")


Checking path: /content/drive/My Drive/VisionAI/Final_Project/yelp-dataset/photos/ydm3g1wUWSxJnMPgHk2JhQ.jpg
✅ FILE EXISTENCE CHECK: File is present at the specified path.
Size: 243 bytes.
❌ INTEGRITY CHECK: PIL FAILED to read the file structure.
   Reason: cannot identify image file '/content/drive/My Drive/VisionAI/Final_Project/yelp-dataset/photos/ydm3g1wUWSxJnMPgHk2JhQ.jpg'
   Action: This file is **corrupted** and must be skipped during extraction.

Checking path: /content/drive/My Drive/VisionAI/Final_Project/yelp-dataset/photos/JGpfPj8VEvnq1B-Xqr3w-A.jpg
✅ FILE EXISTENCE CHECK: File is present at the specified path.
Size: 243 bytes.
❌ INTEGRITY CHECK: PIL FAILED to read the file structure.
   Reason: cannot identify image file '/content/drive/My Drive/VisionAI/Final_Project/yelp-dataset/photos/JGpfPj8VEvnq1B-Xqr3w-A.jpg'
   Action: This file is **corrupted** and must be skipped during extraction.

Checking path: /content/drive/My Drive/VisionAI/Final_Project/yelp-dataset/photos

In [ ]:
def get_image_encoder_model(feature_dim):
    # Load ResNet50 base model with ImageNet weights, excluding the classifier
    base_model = ResNet50(weights='imagenet', include_top=False, input_shape=(224, 224, 3))

    # Add layers to get a fixed-size feature vector
    x = GlobalAveragePooling2D()(base_model.output)
    # The final dense layer to match your desired FEATURE_DIM (256)
    feature_output = Dense(feature_dim, activation='relu')(x)

    # Create the final extraction model
    model = Model(inputs=base_model.input, outputs=feature_output)

    # Freeze the ResNet layers (they are only used for feature extraction, not fine-tuning)
    for layer in base_model.layers:
        layer.trainable = False

    return model

# Create the encoder model
feature_extractor = get_image_encoder_model(FEATURE_DIM)
print(f"ResNet Feature Extractor built. Output dimension: {FEATURE_DIM}")
print("Starting feature extraction...")

# --- 2. Feature Extraction Loop ---
image_features_dict = {}
successful_ids = []

# Get a list of all unique photo IDs to process
photo_ids = df['photo_id']

for photo_id in tqdm(photo_ids, desc="Extracting Features"):
    img_path = os.path.join(photo_path, f"{photo_id}.jpg")

    if os.path.exists(img_path):
        try:
            # 1. Verification Attempt using PIL.Image.open()
            # This is the most robust way to check file integrity
            with Image.open(img_path) as img:
                img.verify() # Check the file structure (read header/metadata)

            # If verification passes, proceed with Keras loading/processing

            # 2. Load and Preprocess Image (using the safe alias)
            img = keras_image_utils.load_img(img_path, target_size=(224, 224))
            img_array = keras_image_utils.img_to_array(img)
            img_array = np.expand_dims(img_array, axis=0)
            img_array = preprocess_input(img_array)

            # 3. Extract Features
            features = feature_extractor.predict(img_array, verbose=0)

            # Store the features
            image_features_dict[photo_id] = features[0]
            successful_ids.append(photo_id)

        # Catch specific errors related to file corruption/unidentified format
        except (UnidentifiedImageError, IOError, OSError, Exception) as e:
            # Skip the bad file and continue the loop
            print(f"Skipping corrupt image {photo_id}. Reason: {e}")
            pass
    else:
        print(f"Image file not found: {img_path}") # You can uncomment this if needed
        pass

# --- 3. Save Features to Disk ---
print(f"\nFeature extraction finished. Successfully processed {len(image_features_dict)} images.")

# Convert the dictionary keys (IDs) and values (features) to NumPy arrays
feature_array = np.array(list(image_features_dict.values()))
id_array = np.array(list(image_features_dict.keys()))

# Save the arrays using numpy.savez (compressed format)
np.savez_compressed(
    output_file,
    features=feature_array,
    photo_ids=id_array
)

print(f"Features saved successfully to: {output_file}")
print(f"Shape of the saved features array: {feature_array.shape}")

ResNet Feature Extractor built. Output dimension: 256
Starting feature extraction...


Extracting Features:   1%|          | 1599/200100 [05:15<6:07:10,  9.01it/s]

Skipping corrupt image ydm3g1wUWSxJnMPgHk2JhQ. Reason: cannot identify image file '/content/drive/My Drive/VisionAI/Final_Project/yelp-dataset/photos/ydm3g1wUWSxJnMPgHk2JhQ.jpg'


Extracting Features:   2%|▏         | 4228/200100 [13:25<5:36:38,  9.70it/s]

Skipping corrupt image JGpfPj8VEvnq1B-Xqr3w-A. Reason: cannot identify image file '/content/drive/My Drive/VisionAI/Final_Project/yelp-dataset/photos/JGpfPj8VEvnq1B-Xqr3w-A.jpg'


...

Skipping corrupt image iX-8Xm2G7meRHUg8qhoL1A. Reason: cannot identify image file '/content/drive/My Drive/VisionAI/Final_Project/yelp-dataset/photos/iX-8Xm2G7meRHUg8qhoL1A.jpg'


Extracting Features: 100%|█████████▉| 199225/200100 [5:48:57<01:13, 11.90it/s]

Skipping corrupt image GWLmPwKeBnh2b_7Kv_LQ7w. Reason: cannot identify image file '/content/drive/My Drive/VisionAI/Final_Project/yelp-dataset/photos/GWLmPwKeBnh2b_7Kv_LQ7w.jpg'


Extracting Features: 100%|██████████| 200100/200100 [5:50:22<00:00,  9.52it/s]



Feature extraction finished. Successfully processed 199992 images.
Features saved successfully to: /content/drive/My Drive/VisionAI/Final_Project/yelp_image_features.npz
Shape of the saved features array: (199992, 256)


In [15]:
data_path = "/content/drive/My Drive/VisionAI/Final_Project/image_feature_extraction.ipynb"
destination_notebook_path = 'image_feature_extraction.ipynb'
uname = "Evelyn_Tr"
!git config --global user.email '$linht.nca@gmail.com@gmail.com'
!git config --global user.name '$CoffeeM00d'

shutil.copyfile(data_path, destination_notebook_path)

from getpass import getpass
password = getpass('Password:')
!git clone https://github.com/CoffeeM00d/vision-ai-project.git
%cd vision-ai-project
# create a file, then add it to stage
!git add data_path
!git commit -m 'commit image_feature_extraction'  # commit in Colab
!git push origin main          # push to github


Password:··········
Cloning into 'vision-ai-project'...
remote: Enumerating objects: 730, done.
remote: Counting objects: 100% (87/87), done.
remote: Compressing objects: 100% (53/53), done.
remote: Total 730 (delta 30), reused 73 (delta 23), pack-reused 643 (from 1)
Receiving objects: 100% (730/730), 61.73 MiB | 32.79 MiB/s, done.
Resolving deltas: 100% (37/37), done.
/content/vision-ai-project/vision-ai-project/vision-ai-project/vision-ai-project
fatal: pathspec 'data_path' did not match any files
On branch main
Your branch is up to date with 'origin/main'.

nothing to commit, working tree clean
fatal: could not read Username for 'https://github.com': No such device or address


In [16]:
import numpy as np

# 1. Load the .npy file
# Replace 'your_file.npy' with the actual name of your .npy file
data  = np.load("/content/drive/My Drive/VisionAI/Final_Project/yelp_image_features.npz")

for key, array in data.items():
      # Construct a filename for the CSV, e.g., 'output_array_name.csv'
      output_filename = f'{key}.csv'

      # Save the array to a CSV file with a comma delimiter
      np.savetxt(output_filename, array, delimiter=',')
      print(f"Saved array '{key}' to {output_filename}")

Saved array 'features' to features.csv


TypeError: Mismatch between array dtype ('<U22') and format specifier ('%.18e')